In [ ]:
#@markdown Check type of GPU and VRAM available.
!nvidia-smi --query-gpu=name,memory.total,memory.free --format=csv,noheader

Tesla V100-SXM2-16GB, 16384 MiB, 16150 MiB


## Install Requirements

In [ ]:
!wget -q https://github.com/ShivamShrirao/diffusers/raw/main/examples/dreambooth/train_dreambooth.py
!wget -q https://github.com/ShivamShrirao/diffusers/raw/main/scripts/convert_diffusers_to_original_stable_diffusion.py
%pip install -qq git+https://github.com/ShivamShrirao/diffusers
%pip install -q -U --pre triton
%pip install -q accelerate transformers ftfy bitsandbytes gradio natsort safetensors xformers

In [ ]:
!pip install diffusers --upgrade
!pip install invisible_watermark accelerate safetensors
!pip install -U xformers --index-url https://download.pytorch.org/whl/cu118

In [ ]:
# Create a hidden directory for Hugging Face token storage
!mkdir -p ~/.huggingface  # Ensure that the Hugging Face directory exists in the home directory

# Set the Hugging Face token value
HUGGINGFACE_TOKEN = "your_token"  # Replace "your_token" with your actual Hugging Face token for authentication

# Store the token in a file inside the Hugging Face directory
!echo -n "{HUGGINGFACE_TOKEN}" > ~/.huggingface/token  # Write the token value to the token file for Hugging Face authentication

## Settings and run

In [ ]:
# Define a flag to control whether the model weights will be saved to Google Drive
save_to_gdrive = True  # Set this to False if you don't want to save to Google Drive

# If saving to Google Drive, mount the drive to access it
if save_to_gdrive:
    from google.colab import drive  # Import Google Colab's drive module
    drive.mount('/content/drive')  # Mount Google Drive to access its files

# Set the name of the model to be used (this can be a specific version like -2 or -v1-5)
MODEL_NAME = "stabilityai/stable-diffusion-2-1"  # Define model name for Stable Diffusion

# Define the directory where the model weights will be saved
OUTPUT_DIR = "stable_diffusion_weights/ocular_disease"  # Relative directory for saving model weights
if save_to_gdrive:
    OUTPUT_DIR = "/content/drive/MyDrive/" + OUTPUT_DIR  # If saving to Google Drive, set path in MyDrive
else:
    OUTPUT_DIR = "/content/" + OUTPUT_DIR  # Otherwise, save in the current directory on Colab

# Print the directory where the weights will be saved for confirmation
print(f"[*] Weights will be saved at {OUTPUT_DIR}")

# Create the output directory if it does not exist
!mkdir -p $OUTPUT_DIR  # Create the specified output directory on the file system

Mounted at /content/drive
[*] Weights will be saved at /content/drive/MyDrive/stable_diffusion_weights/burakai_v2


# Start Training

Use the table below to choose the best flags based on your memory and speed requirements. Tested on Tesla T4 GPU.


| `fp16` | `train_batch_size` | `gradient_accumulation_steps` | `gradient_checkpointing` | `use_8bit_adam` | GB VRAM usage | Speed (it/s) |
| ---- | ------------------ | ----------------------------- | ----------------------- | --------------- | ---------- | ------------ |
| fp16 | 1                  | 1                             | TRUE                    | TRUE            | 9.92       | 0.93         |
| no   | 1                  | 1                             | TRUE                    | TRUE            | 10.08      | 0.42         |
| fp16 | 2                  | 1                             | TRUE                    | TRUE            | 10.4       | 0.66         |
| fp16 | 1                  | 1                             | FALSE                   | TRUE            | 11.17      | 1.14         |
| no   | 1                  | 1                             | FALSE                   | TRUE            | 11.17      | 0.49         |
| fp16 | 1                  | 2                             | TRUE                    | TRUE            | 11.56      | 1            |
| fp16 | 2                  | 1                             | FALSE                   | TRUE            | 13.67      | 0.82         |
| fp16 | 1                  | 2                             | FALSE                   | TRUE            | 13.7       | 0.83          |
| fp16 | 1                  | 1                             | TRUE                    | FALSE           | 15.79      | 0.77         |


Add `--gradient_checkpointing` flag for around 9.92 GB VRAM usage.

remove `--use_8bit_adam` flag for full precision. Requires 15.79 GB with `--gradient_checkpointing` else 17.8 GB.

remove `--train_text_encoder` flag to reduce memory usage further, degrades output quality.

## (Optional) To check if token limit exceeded 77. 
### (Right now, it is no longer a problem.)

In [ ]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("openai/clip-vit-base-patch32")

text =  "Generate a left eye fundus image. The entire eye fundus should be considered as the foreground, and the background (areas outside the eye) should be completely black.In this disease retina is stretched and thinned, with thin blood vessels, a distorted optic nerve head, some folds in the thin retina, and pigmentation at the fovea. Disease:myopia"

token_count = len(tokenizer.tokenize(text))
print("Number of tokens:", token_count)

In [ ]:
concepts_list = [
    {
        "instance_prompt":      "a photo of ocudisHypertension", # Descriptive prompt for the instance image
        "class_prompt":         "Generate a left eye fundus image. The entire eye fundus should be considered as the foreground, and the background (areas outside the eye) should be completely black.In this disease, vascular wall changes, flame-shaped hemorrhages, and cotton-wool spots are seen in retina. Disease: hypertension", # Detailed description for the class image
        "instance_data_dir":    "/content/data/ocudisHypertension",  # Path for storing instance-specific data
        "class_data_dir":       "/content/data/eye_fundus" # Path for storing regularization data (common to all diseases)
    },
    {
        "instance_prompt":      "a photo of ocudisMyopia",
        "class_prompt":         "Generate a left eye fundus image. The entire eye fundus should be considered as the foreground, and the background (areas outside the eye) should be completely black.In this disease retina is stretched and thinned, with thin blood vessels, a distorted optic nerve head, some folds in the thin retina, and pigmentation at the fovea. Disease:myopia",
        "instance_data_dir":    "/content/data/ocudisMyopia",
        "class_data_dir":       "/content/data/eye_fundus"
    },
    {
        "instance_prompt":      "a photo of ocudisCataract",
        "class_prompt":         "Generate a left eye fundus image. The entire eye fundus should be considered as the foreground, and the background (areas outside the eye) should be completely black. This disease clouding the retina. Retina is more opaque and blurry. Blood vessels cannot be seen. Disease:cataract",
        "instance_data_dir":    "/content/data/ocudisCataract",
        "class_data_dir":       "/content/data/eye_fundus"
    },
    {
        "instance_prompt":      "a photo of ocudisGlaucoma",
        "class_prompt":         "Generate a left eye fundus image. The entire eye fundus should be considered as the foreground, and the background (areas outside the eye) should be completely black. Glaucoma can cause the retina to thin. This makes the retina appear lighter in color than a normal retina and blood vessels appear redder than a normal. Disease: glaucoma",
        "instance_data_dir":    "/content/data/ocudisGlaucoma",
        "class_data_dir":       "/content/data/eye_fundus"
    },
    {
        "instance_prompt":      "a photo of ocudisAMD",
        "class_prompt":         "Generate a left eye fundus image. The entire eye fundus should be considered as the foreground, and the background (areas outside the eye) should be completely black.In this disease, retina is less pigmented and more flecked than normal retina. Disease: age-related macular disease",
        "instance_data_dir":    "/content/data/ocudisAMD",
        "class_data_dir":       "/content/data/eye_fundus"
    }
]

# `class_data_dir` contains regularization images, and the `instance_data_dir` will store specific disease-related images

import json
import os

# Loop to create directories for each instance data directory (one for each disease)
for c in concepts_list:
    os.makedirs(c["instance_data_dir"], exist_ok=True)  # Create directories for storing instance data (disease-specific)

# Save the list of concepts (diseases) into a JSON file for later reference
with open("concepts_list.json", "w") as f:
    json.dump(concepts_list, f, indent=4)  # Write the concepts list to a JSON file for easy loading and reuse

In [ ]:
#@markdown Upload your images by running this cell.

#@markdown OR

#@markdown You can use the file manager on the left panel to upload (drag and drop) to each `instance_data_dir` (it uploads faster). You can also upload your own class images in `class_data_dir` if u don't wanna generate with SD.

# Upload images for each disease concept, either via drag and drop or Colab file upload

from google.colab import files
import shutil  # For moving files to the desired directory

# Loop through each concept (disease) defined in the `concepts_list`
for c in concepts_list:
    print(f"Uploading instance images for `{c['instance_prompt']}`")  # Print the current disease being processed

    # Use Colab's file upload feature to upload images
    uploaded = files.upload()  # Open file upload interface

    # For each uploaded file, move it to the appropriate `instance_data_dir`
    for filename in uploaded.keys():
        dst_path = os.path.join(c['instance_data_dir'], filename)  # Define the destination path for the uploaded file
        shutil.move(filename, dst_path)  # Move the uploaded file to the correct directory


Uploading instance images for `a photo of oculardisease`


In [ ]:
!python3 train_dreambooth.py \
  --pretrained_model_name_or_path=$MODEL_NAME \
  --pretrained_vae_name_or_path="stabilityai/sd-vae-ft-mse" \
  --output_dir=$OUTPUT_DIR \
  --revision="fp16" \
  --with_prior_preservation --prior_loss_weight=1.0 \
  --seed=1337 \
  --resolution=512 \
  --train_batch_size=1 \
  --train_text_encoder \
  --mixed_precision="fp16" \
  --use_8bit_adam \
  --gradient_accumulation_steps=1 \
  --learning_rate=1e-6 \
  --lr_scheduler="constant" \
  --lr_warmup_steps=0 \
  --num_class_images=50 \
  --sample_batch_size=4 \
  --max_train_steps=2000 \
  --save_interval=1000 \
  --save_sample_prompt="a photo of ocudisAMD" \
  --concepts_list="concepts_list.json"

# pretrained_model_name_or_path=$MODEL_NAME \  # Specify the base model to fine-tune
# pretrained_vae_name_or_path="stabilityai/sd-vae-ft-mse" \  # Specify the pretrained VAE model for fine-tuning
# output_dir=$OUTPUT_DIR \  # Define the directory where model weights and outputs will be saved
# revision="fp16" \  # Use 16-bit floating point precision for training to reduce memory usage
# with_prior_preservation --prior_loss_weight=1.0 \  # Enable prior preservation and set its weight (helps prevent overfitting)
# seed=1337 \  # Set a seed for reproducibility
# resolution=512 \  # Set image resolution for training (square images of 512x512 pixels)
# train_batch_size=1 \  # Set the batch size for training
# train_text_encoder \  # Include the text encoder during training (for text-to-image models)
# mixed_precision="fp16" \  # Enable mixed precision training to speed up and reduce memory usage
# use_8bit_adam \  # Use 8-bit Adam optimizer (reduces memory usage and speeds up training)
# gradient_accumulation_steps=1 \  # Set gradient accumulation steps to 1 (no accumulation)
# learning_rate=1e-6 \  # Set the learning rate to 1e-6 (small rate to avoid overfitting)
# lr_scheduler="constant" \  # Use a constant learning rate scheduler
# lr_warmup_steps=0 \  # No warmup steps for the learning rate
# num_class_images=50 \  # Use 50 class images for fine-tuning (can be adjusted based on dataset size)
# sample_batch_size=4 \  # Set batch size for generating samples during training
# max_train_steps=2000 \  # Maximum number of training steps (iterations)
# save_interval=1000 \  # Interval (in steps) at which to save the model's weights
# save_sample_prompt="a photo of ocudisAMD" \  # Prompt to generate sample images for visualization during training
# concepts_list="concepts_list.json"  # Path to the JSON file defining the training concepts (diseases)

# per 10 images, 1000 steps is okay

# Reduce the `--save_interval` to lower than `--max_train_steps` to save weights from intermediate steps.
# `--save_sample_prompt` can be same as `--instance_prompt` to generate intermediate samples (saved along with weights in samples directory).

In [ ]:
#@markdown Specify the weights directory to use (leave blank for latest)

# Set the path for the weights directory, defaulting to a specific folder in Google Drive
WEIGHTS_DIR = "/content/drive/MyDrive/stable_diffusion_weights" #@param {type:"string"}
# Check if the user has left the directory field blank
if WEIGHTS_DIR == "":
    # If the directory path is empty, find the latest directory by using natural sorting
    from natsort import natsorted
    from glob import glob
    # Use glob to list all directories in the OUTPUT_DIR path and sort them naturally
    # The `[-1]` selects the most recent directory
    WEIGHTS_DIR = natsorted(glob(OUTPUT_DIR + os.sep + "*"))[-1]
# Print the final directory being used for weights, either provided or automatically determined
print(f"[*] WEIGHTS_DIR={WEIGHTS_DIR}")

In [ ]:
#@markdown Run to generate a grid of preview images from the last saved weights.
import matplotlib.pyplot as plt
import matplotlib.image as mpimg

# Set the folder where the output weights are stored
weights_folder = OUTPUT_DIR

# Get the list of subfolders in the weights folder, skipping the folder named "0"
# Then sort them based on their numeric values
folders = sorted([f for f in os.listdir(weights_folder) if f != "0"], key=lambda x: int(x))

# Determine the number of rows and columns for the grid based on the number of folders and images in the first folder
row = len(folders)
col = len(os.listdir(os.path.join(weights_folder, folders[0], "samples")))

# Set the scale factor for the image size in the grid
scale = 4

# Create a grid of subplots with the determined number of rows and columns
fig, axes = plt.subplots(row, col, figsize=(col*scale, row*scale), gridspec_kw={'hspace': 0, 'wspace': 0})

# Loop through each folder to display images from the "samples" subfolder
for i, folder in enumerate(folders):
    folder_path = os.path.join(weights_folder, folder)
    image_folder = os.path.join(folder_path, "samples")
    images = [f for f in os.listdir(image_folder)]

    # Loop through each image in the folder
    for j, image in enumerate(images):
        # If there is only one row, use a 1D axis array, else use a 2D grid
        if row == 1:
            currAxes = axes[j]
        else:
            currAxes = axes[i, j]

        # Set the title for the first row of images
        if i == 0:
            currAxes.set_title(f"Image {j}")

        # Set the label for the first column of each image (the folder name)
        if j == 0:
            currAxes.text(-0.1, 0.5, folder, rotation=0, va='center', ha='center', transform=currAxes.transAxes)

        # Get the full path to the image and read it
        image_path = os.path.join(image_folder, image)
        img = mpimg.imread(image_path)

        # Display the image in the current axis and remove the axis labels
        currAxes.imshow(img, cmap='gray')
        currAxes.axis('off')

# Adjust the layout to avoid overlap of subplots
plt.tight_layout()

# Save the generated grid of images as a PNG file
plt.savefig('grid.png', dpi=72)


## Convert weights to ckpt to use in web UIs like AUTOMATIC1111.

In [ ]:
#@markdown Run conversion.
ckpt_path = WEIGHTS_DIR + "/model.ckpt" # Set the path to the checkpoint file where the converted model will be saved

half_arg = "" # Initialize a variable to store conversion arguments (empty initially)
#@markdown  Whether to convert to fp16, takes half the space (2GB).
fp16 = True #@param {type: "boolean"}
# Whether to convert the model to fp16, which takes half the space (2GB)
# If fp16 is enabled, set the argument for the conversion script to use fp16
if fp16:
    half_arg = "--half"

# Run the conversion script, which converts the diffusers model to the original Stable Diffusion checkpoint
!python convert_diffusers_to_original_stable_diffusion.py --model_path $WEIGHTS_DIR  --checkpoint_path $ckpt_path $half_arg
print(f"[*] Converted ckpt saved at {ckpt_path}")

## Inference

In [ ]:
import torch
from torch import autocast
from diffusers import StableDiffusionPipeline, DDIMScheduler
from IPython.display import display

# Set the model path where the trained model is stored (can be in GDrive or local path)
model_path = WEIGHTS_DIR  # If you want to use previously trained model saved in gdrive, replace this with the full path of model in gdrive

# Load the Stable Diffusion model from the pre-trained checkpoint, setting the data type to float16 for GPU efficiency
pipe = StableDiffusionPipeline.from_pretrained(model_path, safety_checker=None, torch_dtype=torch.float16).to("cuda")

# Set the scheduler to DDIM (Denoising Diffusion Implicit Models) to handle the denoising steps during generation
pipe.scheduler = DDIMScheduler.from_config(pipe.scheduler.config)

# Enable memory-efficient attention mechanism for better GPU utilization during inference
pipe.enable_xformers_memory_efficient_attention()

# Define a variable for GPU (currently not used)
g_cuda = None

In [ ]:
#@markdown Can set random seed here for reproducibility.
g_cuda = torch.Generator(device='cuda') # Set up a CUDA generator for reproducibility of random operations on the GPU
num = random.randint(0,3000000) # Generate a random integer between 0 and 3,000,000 to use as a seed for randomness
# Set the seed value manually for reproducibility
seed = num #@param {type:"number"}
g_cuda.manual_seed(seed) # Apply the seed to the CUDA generator to ensure reproducible random numbers on the GPU
num

2737770

In [ ]:
# Set the environment variable to make CUDA operations synchronous for debugging.
# This will make the GPU operations block until they are finished, allowing you to track errors more easily.
os.environ["CUDA_LAUNCH_BLOCKING"] = "1"

# Clear any unused memory cached by CUDA on the GPU to free up space.
# This is useful to prevent running out of memory when repeatedly training or running inference with large models.
torch.cuda.empty_cache()

In [ ]:
#@title Run for generating images.

# Define the text prompt for generating the image. This will guide the model in creating the desired image.
prompt = "a photo of ocudisAMD." #@param {type:"string"}
# Define the negative prompt to avoid generating undesired features in the image.
# This list of terms helps filter out unwanted characteristics such as low quality, text, cartoonish features, etc.
negative_prompt = "3D, Blurry, Cropped, Draft, Duplicate, Fault, Flaw, Improper scale, Incorrect ratio, Indistinct, Low quality, Low resolution, Mark, Mistake, Replicate, Reproduce, Shortened, Split image, Squint, Storyboard, Text, Unfocused, Cartoon, Childish, Duplicated features" #@param {type:"string"}
# Set the number of samples to generate for the given prompt. 
num_samples = 4 #@param {type:"number"}
# Guidance scale determines how strongly the generated image should follow the given prompt.
# A higher value leads to more adherence to the prompt.
guidance_scale = 8 #@param {type:"number"}
# Number of inference steps that control how detailed and refined the generated image will be.
# More steps usually mean a higher quality image, but take longer to generate.
num_inference_steps = 50 #@param {type:"number"}
# Set the height and width of the generated images.
# These values must be compatible with the model’s expected input resolution (512x512 in this case).
height = 512 #@param {type:"number"}
width = 512 #@param {type:"number"}

# Generate the image using the StableDiffusion pipeline.
# Using autocast and inference_mode for optimized memory usage and speed on the GPU.
with autocast("cuda"), torch.inference_mode():
    # Run the image generation process using the pipeline and the given parameters.
    # The generator is set to `g_cuda` to ensure reproducibility with a fixed random seed.
    images = pipe(
        prompt,                          # The positive prompt for image generation.
        height=height,                    # Set the height of the image.
        width=width,                      # Set the width of the image.
        negative_prompt=negative_prompt,  # The negative prompt to filter unwanted features.
        num_images_per_prompt=num_samples, # Number of images to generate per prompt.
        num_inference_steps=num_inference_steps, # The number of inference steps.
        guidance_scale=guidance_scale,    # How strongly the generated image should follow the prompt.
        generator=g_cuda                  # The random seed generator for reproducibility.
    ).images  # The result will be a list of generated images.

# Display each generated image.
# This will show all the images produced by the pipeline based on the prompt.
for img in images:
     display(img)


# For Mass Data Production

In [ ]:
# Clear any unused memory cached by CUDA on the GPU to free up space.
# This is useful to prevent running out of memory when repeatedly training or running inference with large models.
torch.cuda.empty_cache()

In [ ]:
#@markdown Can set random seed here for reproducibility.
g_cuda = torch.Generator(device='cuda') # Set up a CUDA generator for reproducibility of random operations on the GPU
num = random.randint(0,3000000) # Generate a random integer between 0 and 3,000,000 to use as a seed for randomness
# Set the seed value manually for reproducibility
seed = num #@param {type:"number"}
g_cuda.manual_seed(seed) # Apply the seed to the CUDA generator to ensure reproducible random numbers on the GPU
num

887953

In [ ]:
# Define the text prompt for generating images. This will guide the model to create the desired image.
prompt = "a photo of ocudisCataract"  # The specific prompt for generating images related to Cataract disease

# Negative prompt (none in this case, can be used to filter out unwanted features)
negative_prompt = ""

# Set the number of images to generate per prompt
num_samples = 10  # Number of images generated for each batch

# Define other generation parameters
guidance_scale = 8  # Controls the adherence to the prompt. Higher value means more adherence.
num_inference_steps = 50  # The number of steps to generate the image. More steps = better quality, but takes longer.
height = 512  # Height of the output image (in pixels)
width = 512  # Width of the output image (in pixels)

# Folder to save the generated images to Google Drive
folder_id = "/content/drive/MyDrive/Ocular_Disease/sd_outputs/Cataract"

# Total number of images to generate
total_images = 1250  # Total images required for the batch processing
batch_size = 10  # The number of images to generate per iteration

# Calculate the number of iterations required to generate all the images
num_iterations = total_images // batch_size

# Loop through each iteration to generate and save the images
for iteration in range(num_iterations):
    print(f"Iteration: {iteration + 1}")  # Print the current iteration number

    # Generate images using the Stable Diffusion pipeline
    # Using autocast and inference_mode for efficient memory usage on GPU
    with autocast("cuda"), torch.inference_mode():
        images = pipe(
            prompt,                         # The positive prompt (description for image generation)
            height=height,                   # Image height
            width=width,                     # Image width
            negative_prompt=negative_prompt, # Negative prompt (filters undesired content)
            num_images_per_prompt=num_samples,  # Number of images per prompt
            num_inference_steps=num_inference_steps,  # Inference steps for image generation
            guidance_scale=guidance_scale,   # How closely the image should match the prompt
            generator=g_cuda                 # Use the random seed generator for reproducibility
        ).images  # Get the generated images

    # Save the generated images
    for i, img in enumerate(images):
        # Calculate the image index to uniquely identify each generated image
        image_index = iteration * batch_size + i

        # Save the image to Google Drive
        img.save(folder_id + f'/Cataract_{image_index}.png')
        print(f'Saved Cataract_{image_index}.png to Google Drive')  # Print confirmation message

    # Clear the images from memory
    for i, img in enumerate(images):
        del images[i]  # Release the image tensor from memory

    # Clear the GPU memory cache to avoid out-of-memory errors
    torch.cuda.empty_cache()

    # Generate a new random seed for the next iteration to ensure reproducibility
    num = random.randint(0, 3000000)  # Generate a random number
    seed = num  # Assign the random number as the seed
    g_cuda = torch.Generator(device='cuda')  # Initialize a new random generator for the GPU
    g_cuda.manual_seed(seed)  # Set the seed to ensure consistent image generation

    # Pause for 5 seconds to allow GPU memory to clear before the next iteration
    time.sleep(5)


In [ ]:
# Clear any unused memory cached by CUDA on the GPU to free up space.
# This is useful to prevent running out of memory when repeatedly training or running inference with large models.
torch.cuda.empty_cache()

In [ ]:
#@markdown Run Gradio UI for generating images.
import gradio as gr

# Define the inference function to generate images based on the user's input
def inference(prompt, negative_prompt, num_samples, height=512, width=512, num_inference_steps=50, guidance_scale=7.5):
    # Using autocast for mixed precision and disabling gradients to save memory
    with torch.autocast("cuda"), torch.inference_mode():
        # Generate images with the provided parameters
        return pipe(
            prompt, 
            height=int(height), 
            width=int(width),
            negative_prompt=negative_prompt,
            num_images_per_prompt=int(num_samples),
            num_inference_steps=int(num_inference_steps), 
            guidance_scale=guidance_scale,
            generator=g_cuda  # Use the pre-set random seed for reproducibility
        ).images  # Return the generated images

# Define the Gradio UI interface
with gr.Blocks() as demo:
    with gr.Row():  # Create a row for layout
        with gr.Column():  # First column for input controls
            prompt = gr.Textbox(label="Prompt", value="photo of a dog in a car")  # Textbox for input prompt
            negative_prompt = gr.Textbox(label="Negative Prompt", value="")  # Textbox for negative prompt
            run = gr.Button(value="Generate")  # Button to trigger image generation

            # Row for additional input controls
            with gr.Row():
                num_samples = gr.Number(label="Number of Samples", value=4)  # Number input for number of images to generate
                guidance_scale = gr.Number(label="Guidance Scale", value=7.5)  # Number input for guidance scale

            # Row for image size settings
            with gr.Row():
                height = gr.Number(label="Height", value=512)  # Height of the generated images
                width = gr.Number(label="Width", value=512)  # Width of the generated images

            # Slider for the number of inference steps
            num_inference_steps = gr.Slider(label="Steps", value=24)

        with gr.Column():  # Second column for output display
            gallery = gr.Gallery()  # Gallery component to display generated images

    # Set the button click event to call the inference function and output the results to the gallery
    run.click(inference, inputs=[prompt, negative_prompt, num_samples, height, width, num_inference_steps, guidance_scale], outputs=gallery)

# Launch the Gradio interface
demo.launch(debug=True)  # Launch with debug mode enabled to see potential issues

In [ ]:
#@title (Optional) Delete diffuser and old weights and only keep the ckpt to free up drive space.

#@markdown [ ! ] Caution, Only execute if you are sure u want to delete the diffuser format weights and only use the ckpt.

# Loop through all files in the OUTPUT_DIR and delete those that are not in the WEIGHTS_DIR (keeping only the checkpoint)
for f in glob(OUTPUT_DIR + os.sep + "*"):  # Iterate through all files and directories in OUTPUT_DIR
    if f != WEIGHTS_DIR:  # Skip the WEIGHTS_DIR folder
        shutil.rmtree(f)  # Delete the file/folder
        print("Deleted", f)  # Print confirmation message for deletion

# Loop through all files in WEIGHTS_DIR and delete everything except the `.ckpt` and `.json` files
for f in glob(WEIGHTS_DIR + "/*"):  # Iterate through all files in the WEIGHTS_DIR
    if not f.endswith(".ckpt") and not f.endswith(".json"):  # Check if the file is not a .ckpt or .json file
        try:
            shutil.rmtree(f)  # Attempt to delete non-.ckpt and non-.json files
        except NotADirectoryError:  # Handle case where the file is not a directory
            continue  # Skip to the next file if an error occurs (such as if it's not a directory)
        print("Deleted", f)  # Print confirmation message for deletion


In [ ]:
#@title Free runtime memory
exit()